# 1. Producing the data
In this task, we will implement one Apache Kafka producer to simulate real-time data streaming. Spark is not allowed in this part since it’s simulating a streaming data source.

1) Your program should send one batch of click_stream data every 1 second to the Kafka stream. One batch consists of a 200 rows from the click_stream_rt dataset. The CSV shouldn’t be loaded to memory at once to conserve memory (i.e. Read row as needed).
2) For each row, add a timestamp column named ‘ts’ in Unix timestamp format. This is the event time when you send the streaming data, which should be in int format. The ‘ts’ should be the same for the data sent in one batch (every 1 second).
3) Let X presents a particular batch of records to be sent. Fig. 1 depicts a sequence of data batches and the data structures.
4) Send the data batch X1, X2, X3…. to a Kafka topic with an appropriate name.
 


In [1]:
import time
import csv
from kafka3 import KafkaProducer
import json
from datetime import datetime

hostip = "192.168.0.3"
topic_name = 'click_stream_topic'
file_path = 'click_stream_rt.csv'

def get_current_timestamp():
    return int(datetime.now().timestamp())

def readCSVFile(file_path):
    data_list = []
    with open(file_path, 'r') as file:
        reader = csv.DictReader(file)
        for row in reader:
            row.pop('#', None)  # Remove the first column
            data_list.append(row)
    return data_list

def publish_message(producer_instance, topic_name, data):
    try:
        producer_instance.send(topic_name, value=data)
        producer_instance.flush()
        print('Message published successfully. Data: ' + str(data))
    except Exception as ex:
        print('Exception in publishing message.')
        print(str(ex))

def connect_kafka_producer():
    _producer = None
    try:
        _producer = KafkaProducer(
            bootstrap_servers=[f'{hostip}:9092'],
            value_serializer=lambda x: json.dumps(x).encode('utf-8'),
            api_version=(0, 10)
        )
    except Exception as ex:
        print('Exception while connecting Kafka.')
        print(str(ex))
    finally:
        return _producer

if __name__ == '__main__':
    # Read data from CSV
    data_rows = readCSVFile(file_path)
    
    print('Publishing records..')
    producer = connect_kafka_producer()
    
    # Sending data continuously
    start_index = 0
    while True:
        current_time = get_current_timestamp()
        
        # Send one batch of 200 rows every second
        for i in range(start_index, len(data_rows), 200):
            batch = data_rows[i:i + 200]
            
            for row in batch:
                row['ts'] = current_time  # Add timestamp to each row
                publish_message(producer, topic_name, row)
            
            time.sleep(1)  # Wait for 1 second before sending the next batch
        
        # Reset to start from beginning
        start_index = 0


Publishing records..
Message published successfully. Data: {'session_id': '00068903-1b05-4256-beab-ce7e2754e3c9', 'event_name': 'ADD_TO_CART', 'event_id': '0a99048f-3c84-4806-8146-2cb7b5a352dd', 'traffic_source': 'WEB', 'event_metadata': "{'product_id': 8949, 'quantity': 1, 'item_price': 223892}", 'customer_id': '38895', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00068903-1b05-4256-beab-ce7e2754e3c9', 'event_name': 'HOMEPAGE', 'event_id': 'db467d8a-12e1-4851-b98b-13af76fe62f2', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '38895', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00068903-1b05-4256-beab-ce7e2754e3c9', 'event_name': 'PURCHASE', 'event_id': 'c34b8c89-590e-4f70-acb6-f29cbc26b610', 'traffic_source': 'WEB', 'event_metadata': "{'payment_status': 'Success'}", 'customer_id': '38895', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00068903-1b05-4256-beab-ce7e2754e3c9', 'event_name': 'SE

Message published successfully. Data: {'session_id': '001ea8df-ba11-41cd-8bcc-2b36bc04ee4c', 'event_name': 'ADD_TO_CART', 'event_id': '650d5672-a794-4dff-9498-a5b6b22d0a1a', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 48843, 'quantity': 1, 'item_price': 239315}", 'customer_id': '44024', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '001ea8df-ba11-41cd-8bcc-2b36bc04ee4c', 'event_name': 'HOMEPAGE', 'event_id': 'dc26e6fb-eac6-481b-b332-3291d1a52624', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '44024', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '001ea8df-ba11-41cd-8bcc-2b36bc04ee4c', 'event_name': 'ADD_TO_CART', 'event_id': '59c656c6-4060-46fc-8bd0-9598e64e39b2', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 23841, 'quantity': 1, 'item_price': 75264}", 'customer_id': '44024', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '001ea8df-ba11-41cd-8bcc-2b36bc04ee4c

Message published successfully. Data: {'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'VIEW_PROMO', 'event_id': '2feb8f61-822d-43ee-b511-8690aa60f97d', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '91500', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'VIEW_PROMO', 'event_id': 'cb4f6a30-7004-4dc9-908d-d8ef38f8cc39', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '91500', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'VIEW_PROMO', 'event_id': '752d70d5-4a9b-418e-8eb2-5ce05722fb96', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '91500', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'VIEW_PROMO', 'event_id': '496716d7-8db2-45b2-94fc-43adfb6d38e2', 'traffic_source': 'MOBILE', 'eve

Message published successfully. Data: {'session_id': '0034d9dd-0ac8-42dc-bbc1-0ecf7ba07607', 'event_name': 'CLICK', 'event_id': '485e7d4e-b243-4e3d-946a-6533302afe1b', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '55459', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0034d9dd-0ac8-42dc-bbc1-0ecf7ba07607', 'event_name': 'VIEW_PROMO', 'event_id': 'f1b8f7d8-c863-44bf-9b03-234d203d9a46', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '55459', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0034d9dd-0ac8-42dc-bbc1-0ecf7ba07607', 'event_name': 'ADD_PROMO', 'event_id': '3ef5eca5-a0b8-448c-9112-b5fc58378e9a', 'traffic_source': 'MOBILE', 'event_metadata': "{'promo_code': 'WEEKENDSERU', 'promo_amount': 3677}", 'customer_id': '55459', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '0034d9dd-0ac8-42dc-bbc1-0ecf7ba07607', 'event_name': 'ADD_TO_CART', 'event_id': '1f88c27e-6e5b-4e74-ae0e-e

Message published successfully. Data: {'session_id': '0045a305-a50a-4a43-97c7-aaeadbc77687', 'event_name': 'HOMEPAGE', 'event_id': '8a9ca346-a1cb-4683-985a-a9227fb3d0d9', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '21034', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00574f08-87f0-4057-a02a-0361e65ed379', 'event_name': 'ADD_TO_CART', 'event_id': '0b583908-29de-432a-acd5-fd198150b12e', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 52414, 'quantity': 1, 'item_price': 212996}", 'customer_id': '70053', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00574f08-87f0-4057-a02a-0361e65ed379', 'event_name': 'VIEW_ITEM', 'event_id': '6813b737-0d50-47fa-9d4d-60928abe1959', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '70053', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '00574f08-87f0-4057-a02a-0361e65ed379', 'event_name': 'PURCHASE', 'event_id': '30b825b4-b379-4bc

...

Message published successfully. Data: {'session_id': '106bdbb4-41fa-4c8a-8b2a-e8a7097fad17', 'event_name': 'VIEW_ITEM', 'event_id': '617e70cf-41d1-45be-8408-53b018d39247', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '25197', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '106bdbb4-41fa-4c8a-8b2a-e8a7097fad17', 'event_name': 'SCROLL', 'event_id': '71c5db95-e0fe-4d06-951c-d924edaca6b6', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '25197', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '106bdbb4-41fa-4c8a-8b2a-e8a7097fad17', 'event_name': 'CLICK', 'event_id': 'aae3a4ce-7055-4c36-9269-0cccfcc44119', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '25197', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '106bdbb4-41fa-4c8a-8b2a-e8a7097fad17', 'event_name': 'VIEW_ITEM', 'event_id': 'cb3d20c6-639f-471d-a452-59889bcff92e', 'traffic_source': 'WEB', 'event_metadata': '', 'cust

Message published successfully. Data: {'session_id': '1082557e-76b3-4f31-8e7d-8bc7d898d062', 'event_name': 'ADD_TO_CART', 'event_id': 'c5bc6caf-9ad5-435c-b7fd-d8851f1819e3', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 18730, 'quantity': 1, 'item_price': 373080}", 'customer_id': '92402', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '1082557e-76b3-4f31-8e7d-8bc7d898d062', 'event_name': 'SEARCH', 'event_id': '00fa299f-a342-4dfc-bb49-b241ca5b69df', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Tas Wanita'}", 'customer_id': '92402', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '1082557e-76b3-4f31-8e7d-8bc7d898d062', 'event_name': 'SEARCH', 'event_id': '4af780c6-a5a1-4838-bfbd-f83fa87826e0', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Tas Kerja'}", 'customer_id': '92402', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '1082557e-76b3-4f31-8e7d-8bc7d898d06

Message published successfully. Data: {'session_id': '108e0d2d-c65c-4e32-a6db-5aa5bcc4d256', 'event_name': 'HOMEPAGE', 'event_id': '20ee80fd-3848-4462-ae3a-46326e462a35', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '17836', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '108e0d2d-c65c-4e32-a6db-5aa5bcc4d256', 'event_name': 'SEARCH', 'event_id': '6c51e188-a2ef-4f59-b903-2a7a5bbd9169', 'traffic_source': 'WEB', 'event_metadata': "{'search_keywords': 'Kaos'}", 'customer_id': '17836', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '108e0d2d-c65c-4e32-a6db-5aa5bcc4d256', 'event_name': 'HOMEPAGE', 'event_id': '44b9aa1c-1678-4b3a-b1b1-e255849a2927', 'traffic_source': 'WEB', 'event_metadata': '', 'customer_id': '17836', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '108e0d2d-c65c-4e32-a6db-5aa5bcc4d256', 'event_name': 'SCROLL', 'event_id': '966ba874-659f-44e0-b6c9-062deca893ab', 'traffic_source': 'WEB', '

Message published successfully. Data: {'session_id': '10a7adc0-02ae-49e8-85fb-8aa054c6d74a', 'event_name': 'SCROLL', 'event_id': 'c98a745a-7854-4a74-b449-8e5eec12b651', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '16922', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '10a7adc0-02ae-49e8-85fb-8aa054c6d74a', 'event_name': 'HOMEPAGE', 'event_id': '517f8634-b6d9-45e0-b69a-fbd830f6f98f', 'traffic_source': 'MOBILE', 'event_metadata': '', 'customer_id': '16922', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '10a7adc0-02ae-49e8-85fb-8aa054c6d74a', 'event_name': 'ADD_TO_CART', 'event_id': '4f011b70-5023-43ae-ad84-df7c3d598bc2', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 15365, 'quantity': 1, 'item_price': 94650}", 'customer_id': '16922', 'ts': 1716732160}
Message published successfully. Data: {'session_id': '10a7adc0-02ae-49e8-85fb-8aa054c6d74a', 'event_name': 'ADD_TO_CART', 'event_id': 'b0236e0e-a0b1-4a4e

KeyboardInterrupt: 